# Отчет о проделанной работе

## Введение

Задача: Написать нейронную сеть для распознования набора данных Cifar10

## Загрузка и предобработка данных

В качестве набора данных для обучения используется набор данных (Cifar10)[https://www.cs.toronto.edu/%7Ekriz/cifar.html]

### Загрузка данных

In [ ]:
(x_train, y_train), (x_test, y_test) = tf.keras.datasets.cifar10.load_data()

### Подготовка данных

In [ ]:
# Нормализация
x_train, x_test = x_train / 255.0, x_test / 255.0

# Аугментация
datagen = ImageDataGenerator(
    rotation_range=15,
    width_shift_range=0.1,
    height_shift_range=0.1,
    horizontal_flip=True
)
datagen.fit(x_train)

## Создание модели

Для решения задачи используется сверточная нейронная сеть (CNN).

### Архитектура модели

1. **Входной слой**:
   - **Тип слоя**: Сверточный слой (Conv2D).
   - **Фильтры**: 32 фильтра.
   - **Размер ядра**: 3x3.
   - **Функция активации**: ReLU (Rectified Linear Unit).

2. **Слой подвыборки (MaxPooling)**:
   - **Тип слоя**: Слой подвыборки (MaxPooling2D).
   - **Размер окна**: 2x2.
   - **Функция**: Уменьшает размерность выходных данных предыдущего слоя вдвое, выбирая максимальное значение в каждом окне 2x2.

3. **Второй сверточный слой**:
   - **Тип слоя**: Сверточный слой (Conv2D).
   - **Фильтры**: 64 фильтра.
   - **Размер ядра**: 3x3.
   - **Функция активации**: ReLU.

4. **Второй слой подвыборки (MaxPooling)**:
   - **Тип слоя**: Слой подвыборки (MaxPooling2D).
   - **Размер окна**: 2x2.
   - **Функция**: Уменьшает размерность выходных данных предыдущего слоя вдвое.

5. **Третий сверточный слой**:
   - **Тип слоя**: Сверточный слой (Conv2D).
   - **Фильтры**: 64 фильтра.
   - **Размер ядра**: 3x3.
   - **Функция активации**: ReLU.

6. **Слой преобразования (Flatten)**:
   - **Тип слоя**: Слой преобразования (Flatten).
   - **Функция**: Преобразует многомерные выходные данные предыдущего слоя в одномерный вектор.

7. **Полносвязный слой (Dense)**:
   - **Тип слоя**: Полносвязный слой (Dense).
   - **Нейроны**: 64 нейрона.
   - **Функция активации**: ReLU.

8. **Выходной слой (Dense)**:
   - **Тип слоя**: Полносвязный слой (Dense).
   - **Нейроны**: 10 нейронов (по одному для каждого класса в CIFAR-10).
   - **Функция активации**: Отсутствует (логиты).

### Объяснение архитектуры

1. **Сверточные слои (Conv2D)**:
   - Сверточные слои используются для извлечения признаков из изображений. Они применяют фильтры к входным данным, чтобы выделить важные характеристики, такие как края, текстуры и формы.
   - В данной архитектуре используются три сверточных слоя с различным количеством фильтров (32, 64, 64), что позволяет модели извлекать все более сложные признаки на каждом уровне.

2. **Слои подвыборки (MaxPooling2D)**:
   - Слои подвыборки уменьшают размерность данных, сохраняя наиболее важные признаки. Это помогает снизить вычислительную сложность и предотвратить переобучение.
   - В данной архитектуре используются два слоя подвыборки, каждый из которых уменьшает размерность данных вдвое.

3. **Слой преобразования (Flatten)**:
   - Слой преобразования преобразует многомерные данные в одномерный вектор, что необходимо для подачи данных в полносвязные слои.

4. **Полносвязные слои (Dense)**:
   - Полносвязные слои используются для классификации извлеченных признаков. Они соединяют все нейроны предыдущего слоя с каждым нейроном текущего слоя.
   - В данной архитектуре используется один полносвязный слой с 64 нейронами и функцией активации ReLU, а также выходной слой с 10 нейронами (по одному для каждого класса).

In [ ]:
model = models.Sequential([
    layers.Conv2D(32, (3, 3), activation='relu', input_shape=(32, 32, 3)),
    layers.MaxPooling2D((2, 2)),
    layers.Conv2D(64, (3, 3), activation='relu'),
    layers.MaxPooling2D((2, 2)),
    layers.Conv2D(64, (3, 3), activation='relu'),
    layers.Flatten(),
    layers.Dense(64, activation='relu'),
    layers.Dense(10)
])

## Компиляция и обучение модели

Предварительно зададим, что будем использовать (оптимизатор)[https://www.tensorflow.org/api_docs/python/tf/keras/optimizers] использующий алгоритм (Adam)[https://www.tensorflow.org/api_docs/python/tf/keras/optimizers/Adam]. [1](https://education.yandex.ru/handbook/ml/article/optimizaciya-v-ml)

В качестве (функции потерь)[https://www.tensorflow.org/api_docs/python/tf/keras/losses] будем использовать функцию (кросс-энтропии)[https://education.yandex.ru/handbook/ml/article/landshaft-funkcii-poter] для эффективного измерения разницы между предсказанными и истинными метками классов хорошо должна подойти (SparseCategoricalCrossentropy)[https://www.tensorflow.org/api_docs/python/tf/keras/losses/SparseCategoricalCrossentropy]

In [ ]:
model.compile(optimizer='adam',
              loss=tf.keras.losses.SparseCategoricalCrossentropy(from_logits=True),
              metrics=['accuracy'])

## Результаты

При такой модели на тестовых данных получено в районе 70% (максимум 71% на 11й эпохе). При этом тренировачные данные показывали 90% на 20й эпохе

## google/vit-base-patch16-224

При попытке использовать готовую модель google/vit-base-patch16-224 точность модель составила 10%. При попытке дообучить модель точность практически не изменилась. Полагаю не разборался как проверить данную модель на данных CIFAR10.

Модель: google/vit-base-patch16-224
Test Accuracy: 0.1000
Classification Report:
              precision    recall  f1-score   support

    airplane       0.10      1.00      0.18      1000
  automobile       0.00      0.00      0.00      1000
        bird       0.00      0.00      0.00      1000
         cat       0.00      0.00      0.00      1000
        deer       0.00      0.00      0.00      1000
         dog       0.00      0.00      0.00      1000
        frog       0.00      0.00      0.00      1000
       horse       0.00      0.00      0.00      1000
        ship       0.00      0.00      0.00      1000
       truck       0.00      0.00      0.00      1000

    accuracy                           0.10     10000
   macro avg       0.01      0.10      0.02     10000
weighted avg       0.01      0.10      0.02     10000

---

Дообученная модель google/vit-base-patch16-224 на данных Cifar10
Test Accuracy: 0.1018
Classification Report:
              precision    recall  f1-score   support

    airplane       0.04      0.01      0.01      1000
  automobile       0.15      0.33      0.21      1000
        bird       0.10      0.07      0.09      1000
         cat       0.11      0.05      0.07      1000
        deer       0.02      0.01      0.01      1000
         dog       0.07      0.07      0.07      1000
        frog       0.25      0.12      0.17      1000
       horse       0.11      0.17      0.14      1000
        ship       0.03      0.06      0.04      1000
       truck       0.16      0.12      0.14      1000

    accuracy                           0.10     10000
   macro avg       0.11      0.10      0.09     10000
weighted avg       0.11      0.10      0.09     10000